In [1]:
from dataset.build_dataset import build_dataset
import mindspore.dataset as ds
import os
import numpy as np
from mindspore.mindrecord import FileWriter
import json

[WARNING] ME(26762:140123606165312,MainProcess):2021-10-26-11:36:32.410.512 [mindspore/run_check/_check_version.py:181] Cuda ['10.1', '11.1'] version(need by mindspore-gpu) is not found, please confirm that the path of cuda is set to the env LD_LIBRARY_PATH, please refer to the installation guidelines: https://www.mindspore.cn/install
[WARNING] ME(26762:140123606165312,MainProcess):2021-10-26-11:36:32.419.515 [mindspore/run_check/_check_version.py:181] Cuda ['10.1', '11.1'] version(need by mindspore-gpu) is not found, please confirm that the path of cuda is set to the env LD_LIBRARY_PATH, please refer to the installation guidelines: https://www.mindspore.cn/install


In [2]:
FEATURES_FILE = "./data/train_data.npy"

features = np.load(FEATURES_FILE)
list_dict = []
for item in features:
    dict_temp = json.loads(item)
    list_dict.append(dict_temp)

In [3]:
len(list_dict[0]['word_ids'])

180

In [4]:
list_dict[0]['word_ids']

[0,
 598,
 2661,
 222,
 5,
 9880,
 2708,
 2346,
 2082,
 11,
 504,
 4432,
 11,
 226,
 2126,
 10067,
 1470,
 116,
 2,
 2,
 29474,
 28108,
 6,
 5,
 334,
 34,
 10,
 4019,
 2048,
 4,
 497,
 1517,
 5,
 4326,
 6919,
 18,
 1637,
 31346,
 16,
 10,
 9030,
 9577,
 9,
 5,
 9880,
 2708,
 4,
 29261,
 11,
 760,
 9,
 5,
 4326,
 6919,
 8,
 2114,
 24,
 6,
 16,
 10,
 7621,
 9577,
 9,
 4845,
 19,
 3701,
 62,
 33161,
 19,
 5,
 7875,
 22,
 39043,
 1459,
 1614,
 1464,
 13292,
 4977,
 845,
 4130,
 7,
 5,
 4326,
 6919,
 16,
 5,
 26429,
 2426,
 9,
 5,
 25095,
 6924,
 4,
 29261,
 639,
 5,
 32394,
 2426,
 16,
 5,
 7461,
 26187,
 6,
 10,
 19035,
 317,
 9,
 9621,
 8,
 12456,
 4,
 85,
 16,
 10,
 24633,
 9,
 5,
 11491,
 26187,
 23,
 226,
 2126,
 10067,
 6,
 1470,
 147,
 5,
 9880,
 2708,
 2851,
 13735,
 352,
 1382,
 7,
 6130,
 6552,
 625,
 3398,
 208,
 22895,
 853,
 1827,
 11,
 504,
 4432,
 4,
 497,
 5,
 253,
 9,
 5,
 1049,
 1305,
 36,
 463,
 11,
 10,
 2228,
 516,
 14,
 15230,
 149,
 155,
 19638,
 8,
 5,
 2610,
 25336

In [5]:
SQUAD_MINDRECORD_FILE = "./data/train_features.mindrecord"

In [6]:
pad = lambda a,i : a[0:i] if len(a) > i else a + [0] * (i-len(a))
pad1 = lambda a,i : a[0:i] if len(a) > i else a + [1] * (i-len(a))
pad_entity = lambda a,i : a[0:i] if len(a) > i else np.append(a,[-1] * (i-len(a)))

for slist in list_dict:
    slist["entity_attention_mask"] = pad(slist["entity_attention_mask"], 24)
    slist["entity_ids"] = pad(slist["entity_attention_mask"], 24)
    slist["entity_segment_ids"] = pad(slist["entity_segment_ids"], 24)
    
    slist["word_ids"] = pad1(slist["word_ids"], 512)
    slist["word_segment_ids"] = pad(slist["word_segment_ids"], 512)
    slist["word_attention_mask"] = pad(slist["word_attention_mask"], 512)
    # entity padding 1
    entity_size = len(slist["entity_position_ids"])
    slist["entity_position_ids"] = np.array(slist["entity_position_ids"])
    temp = [[-1]*24 for i in range(24)]
    for i in range(24):
        if i < entity_size-1:
            temp[i]=(pad_entity(slist["entity_position_ids"][i], 24))


    slist["entity_position_ids"] =temp
    # entity_padding 2
    #slist["entity_position_ids"] = np.array(slist["entity_position_ids"]).flatten()
    #slist["entity_position_ids"] = pad_entity(slist["entity_position_ids"], 24)


if os.path.exists(SQUAD_MINDRECORD_FILE):
    os.remove(SQUAD_MINDRECORD_FILE)
    os.remove(SQUAD_MINDRECORD_FILE + ".db")

writer = FileWriter(file_name=SQUAD_MINDRECORD_FILE, shard_num=1)

data_schema = {
    #"unique_id": {"type": "int32", "shape": [-1]},
    "word_ids": {"type": "int32", "shape": [-1]},
    "word_segment_ids": {"type": "int32", "shape": [-1]},
    "word_attention_mask": {"type": "int32", "shape": [-1]},
    "entity_ids": {"type": "int32", "shape": [-1]},
    "entity_position_ids": {"type": "int32", "shape": [24,24]}, # 
    "entity_segment_ids": {"type": "int32", "shape": [-1]},
    "entity_attention_mask": {"type": "int32", "shape": [-1]},
    "start_positions": {"type": "int32", "shape": [-1]},
    "end_positions": {"type": "int32", "shape": [-1]}
}
writer.add_schema(data_schema, "it is a preprocessed squad dataset")

data = []
i = 0
for item in list_dict:
    i += 1
    sample = {
        #"unique_id": np.array(item["unique_id"], dtype=np.int32),
        "word_ids": np.array(item["word_ids"], dtype=np.int32),
        "word_segment_ids": np.array(item["word_segment_ids"], dtype=np.int32),
        "word_attention_mask": np.array(item["word_attention_mask"], dtype=np.int32),
        "entity_ids": np.array(item["entity_ids"], dtype=np.int32),
        "entity_position_ids": np.array(item["entity_position_ids"], dtype=np.int32),
        "entity_segment_ids": np.array(item["entity_segment_ids"], dtype=np.int32),
        "entity_attention_mask": np.array(item["entity_attention_mask"], dtype=np.int32),
        "start_positions": np.array(item["start_positions"], dtype=np.int32),
        "end_positions": np.array(item["end_positions"], dtype=np.int32),
    }

    data.append(sample)
    #print(sample)
    if i % 10 == 0:
        writer.write_raw_data(data)
        data = []
print(data[0])
if data:
    writer.write_raw_data(data)

writer.commit()

{'word_ids': array([    0,  1740,    99,   343,   473,  1586,  1071, 19252,   904,
         786,  8287,  4871,     7, 15359, 14785,   257,   116,     2,
           2,    20,  1049,   758,  3062,  2754, 15359, 14785,   257,
           8,  4634, 15377,    16,     5, 24311,  6455,  9965,  1016,
        4414,     6,  2034,    59,   411,  8130,    36,   401,  6301,
          36,   246,     4,   406, 11163, 35122,    31,     5,   343,
        2100,     4, 23701,  1070,    30,     5,  5280, 10333,  4305,
           9, 15377,    24,    34,    80, 20531,     6,    65,  1897,
           8,    65,   758,     4,   497,  1455,     6,    59,   820,
         758,  8537,  4686, 15377,     7,    97, 11633,    11,  1005,
           6,  1817,     8,     5,  2367,   953,     6,     7,  1947,
         215,    25, 12275,     6,  3534,     6,   229, 14024,  2186,
           6,  2920,     6, 15398,     6, 18959, 19193,     6,  8086,
        5870,     6, 12600,     6,  2884,   139,     6,   226,  7333,
       

MSRStatus.SUCCESS

In [7]:
output_features = np.array(list_dict)

In [8]:
columns_list = ['word_ids',  'word_segment_ids', 'word_attention_mask',
               'entity_ids', 'entity_position_ids', 'entity_segment_ids',
               'entity_attention_mask', 'start_positions', 'end_positions']

#SQUAD_MINDRECORD_FILE = "./data/dev_features.mindrecord"
data_set = ds.MindDataset(dataset_file=SQUAD_MINDRECORD_FILE, columns_list=columns_list)
count = 0
for item in data_set.create_dict_iterator():
    #print(item)
    count += 1
print("Got {} samples".format(count))

Got 87777 samples


In [9]:
data_set = data_set.batch(2)# , drop_remainder=True
data_sample = next(data_set.create_dict_iterator())
data_sample

{'word_ids': Tensor(shape=[2, 512], dtype=Int32, value=
 [[   0,  653,   16 ...    1,    1,    1],
  [   0, 6834,  191 ...    1,    1,    1]]),
 'word_segment_ids': Tensor(shape=[2, 512], dtype=Int32, value=
 [[0, 0, 0 ... 0, 0, 0],
  [0, 0, 0 ... 0, 0, 0]]),
 'word_attention_mask': Tensor(shape=[2, 512], dtype=Int32, value=
 [[1, 1, 1 ... 0, 0, 0],
  [1, 1, 1 ... 0, 0, 0]]),
 'entity_ids': Tensor(shape=[2, 24], dtype=Int32, value=
 [[1, 1, 0 ... 0, 0, 0],
  [0, 0, 0 ... 0, 0, 0]]),
 'entity_position_ids': Tensor(shape=[2, 24, 24], dtype=Int32, value=
 [[[12, 13, 14 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1],
   ...
   [-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1]],
  [[-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1],
   ...
   [-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1],
   [-1, -1, -1 ... -1, -1, -1]]]),
 'entity_segment_ids': Tensor(shape=[2, 

In [10]:
data_sample['entity_position_ids']

Tensor(shape=[2, 24, 24], dtype=Int32, value=
[[[12, 13, 14 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  ...
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1]],
 [[-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  ...
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1]]])

In [11]:
data_sample['entity_attention_mask']

Tensor(shape=[2, 24], dtype=Int32, value=
[[1, 1, 0 ... 0, 0, 0],
 [0, 0, 0 ... 0, 0, 0]])

## Train

In [12]:
from readingcomprehension.models.luke import LukeForReadingComprehension, LukeForReadingComprehensionWithLoss, LukeEntityAwareAttentionModel, LukeSquadCell
import mindspore.common.dtype as mstype
from model.bert_model import BertConfig
from mindspore import context, save_checkpoint
from model.luke import LukeModel, EntityAwareEncoder
from mindspore import Tensor, context
from mindspore import dtype as mstype
import mindspore.ops as ops
import mindspore.nn as nn
from model.bert_model import BertOutput
from mindspore.common.initializer import TruncatedNormal
from mindspore.ops import composite as C
import mindspore
from mindspore.ops import operations as P
from mindspore.train.model import Model
from tqdm import tqdm
from mindspore.train.serialization import load_checkpoint, load_param_into_net
from mindspore.train.model import Model
import collections
# PYNATIVE_MODE & GRAPH_MODE
context.set_context(mode=context.GRAPH_MODE, device_target="GPU")
context.set_context(enable_graph_kernel=True)

In [13]:

# def do_train(dataset=None, network=None, load_checkpoint_path="", save_checkpoint_path="", epoch_num=1):
#     """ do train """
#     if load_checkpoint_path == "":
#         raise ValueError("Pretrain model missed, finetune task must load pretrain model!")
#     steps_per_epoch = dataset.get_dataset_size()
#     # optimizer
#     if optimizer_cfg.optimizer == 'AdamWeightDecay':
#         lr_schedule = BertLearningRate(learning_rate=15e-6,
#                                        end_learning_rate=optimizer_cfg.AdamWeightDecay.end_learning_rate,
#                                        warmup_steps=int(steps_per_epoch * epoch_num * 0.1),
#                                        decay_steps=steps_per_epoch * epoch_num,
#                                        power=optimizer_cfg.AdamWeightDecay.power)
#         params = network.trainable_params()
#         decay_params = list(filter(optimizer_cfg.AdamWeightDecay.decay_filter, params))
#         other_params = list(filter(lambda x: not optimizer_cfg.AdamWeightDecay.decay_filter(x), params))
#         group_params = [{'params': decay_params, 'weight_decay': optimizer_cfg.AdamWeightDecay.weight_decay},
#                         {'params': other_params, 'weight_decay': 0.0}]

#         optimizer = AdamWeightDecay(group_params, lr_schedule, eps=optimizer_cfg.AdamWeightDecay.eps)
#     elif optimizer_cfg.optimizer == 'Lamb':
#         lr_schedule = BertLearningRate(learning_rate=optimizer_cfg.Lamb.learning_rate,
#                                        end_learning_rate=optimizer_cfg.Lamb.end_learning_rate,
#                                        warmup_steps=int(steps_per_epoch * epoch_num * 0.1),
#                                        decay_steps=steps_per_epoch * epoch_num,
#                                        power=optimizer_cfg.Lamb.power)
#         optimizer = Lamb(network.trainable_params(), learning_rate=lr_schedule)
#     elif optimizer_cfg.optimizer == 'Momentum':
#         optimizer = Momentum(network.trainable_params(), learning_rate=optimizer_cfg.Momentum.learning_rate,
#                              momentum=optimizer_cfg.Momentum.momentum)
#     else:
#         raise Exception("Optimizer not supported. support: [AdamWeightDecay, Lamb, Momentum]")

#     # load checkpoint into network
#     ckpt_config = CheckpointConfig(save_checkpoint_steps=steps_per_epoch, keep_checkpoint_max=1)
#     ckpoint_cb = ModelCheckpoint(prefix="squad",
#                                  directory=None if save_checkpoint_path == "" else save_checkpoint_path,
#                                  config=ckpt_config)
#     param_dict = load_checkpoint(load_checkpoint_path)
#     load_param_into_net(network, param_dict)

#     update_cell = DynamicLossScaleUpdateCell(loss_scale_value=2 ** 32, scale_factor=2, scale_window=1000)
#     netwithgrads = BertSquadCell(network, optimizer=optimizer, scale_update_cell=update_cell)
#     model = Model(netwithgrads)
#     callbacks = [TimeMonitor(dataset.get_dataset_size()), LossCallBack(dataset.get_dataset_size()), ckpoint_cb]
#     model.train(epoch_num, dataset, callbacks=callbacks)

In [14]:
from mindspore.train.callback import Callback
from mindspore.train.serialization import load_checkpoint, load_param_into_net
from mindspore.train.model import Model
from mindspore.nn.learning_rate_schedule import LearningRateSchedule, PolynomialDecayLR, WarmUpLR
from mindspore.nn.wrap.loss_scale import DynamicLossScaleUpdateCell

import collections
import time
class BertLearningRate(LearningRateSchedule):
    """
    Warmup-decay learning rate for Bert network.
    """

    def __init__(self, learning_rate, end_learning_rate, warmup_steps, decay_steps, power):
        super(BertLearningRate, self).__init__()
        self.warmup_flag = False
        if warmup_steps > 0:
            self.warmup_flag = True
            self.warmup_lr = WarmUpLR(learning_rate, warmup_steps)
        self.decay_lr = PolynomialDecayLR(learning_rate, end_learning_rate, decay_steps, power)
        self.warmup_steps = Tensor(np.array([warmup_steps]).astype(np.float32))

        self.greater = mindspore.ops.Greater()
        self.one = Tensor(np.array([1.0]).astype(np.float32))
        self.cast = mindspore.ops.Cast()

    def construct(self, global_step):
        decay_lr = self.decay_lr(global_step)
        if self.warmup_flag:
            is_warmup = self.cast(self.greater(self.warmup_steps, global_step), mstype.float32)
            warmup_lr = self.warmup_lr(global_step)
            lr = (self.one - is_warmup) * decay_lr + is_warmup * warmup_lr
        else:
            lr = decay_lr
            
        
        return lr


class LossCallBack(Callback):
    """
    Monitor the loss in training.

    If the loss is NAN or INF terminating training.

    Note:
        If per_print_times is 0 do not print loss.

    Args:
        per_print_times (int): Print loss every times. Default: 1.
    """

    def __init__(self, per_print_times=1, rank_ids=0):
        super(LossCallBack, self).__init__()
        if not isinstance(per_print_times, int) or per_print_times < 0:
            raise ValueError("print_step must be int and >= 0.")
        self._per_print_times = per_print_times
        self.rank_id = rank_ids
        self.time_stamp_first = get_ms_timestamp()

    def step_end(self, run_context):
        """Monitor the loss in training."""
        time_stamp_current = get_ms_timestamp()
        cb_params = run_context.original_args()
        print("time: {}, epoch: {}, step: {}, outputs are {}".format(time_stamp_current - self.time_stamp_first,
                                                                     cb_params.cur_epoch_num,
                                                                     cb_params.cur_step_num,
                                                                     str(cb_params.net_outputs)))
        with open("./loss_{}.log".format(self.rank_id), "a+") as f:
            f.write("time: {}, epoch: {}, step: {}, loss: {}".format(
                time_stamp_current - self.time_stamp_first,
                cb_params.cur_epoch_num,
                cb_params.cur_step_num,
                str(cb_params.net_outputs[0].asnumpy())))
            f.write('\n')


def get_ms_timestamp():
    t = time.time()
    return int(round(t * 1000))

In [15]:
for i in data_set:
    print(len(i))
    print(i)
    break

9
[Tensor(shape=[2, 512], dtype=Int32, value=
[[  0, 653,  16 ...   1,   1,   1],
 [  0, 653,  74 ...   1,   1,   1]]), Tensor(shape=[2, 512], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [0, 0, 0 ... 0, 0, 0]]), Tensor(shape=[2, 512], dtype=Int32, value=
[[1, 1, 1 ... 0, 0, 0],
 [1, 1, 1 ... 0, 0, 0]]), Tensor(shape=[2, 24], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [1, 0, 0 ... 0, 0, 0]]), Tensor(shape=[2, 24, 24], dtype=Int32, value=
[[[-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  ...
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1]],
 [[47, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  ...
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1]]]), Tensor(shape=[2, 24], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [0, 0, 0 ... 0, 0, 0]]), Tensor(shape=[2, 24], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [1, 0, 0 

In [16]:
epoch=1

luke_config = BertConfig()
LUKEModel = LukeForReadingComprehension(luke_config)
#param_dict = load_checkpoint('./luke-large-qa.ckpt')
param_dict = load_checkpoint('./luke-large.ckpt')
load_param_into_net(LUKEModel,param_dict)

# update_cell = DynamicLossScaleUpdateCell(loss_scale_value=2 ** 32, scale_factor=2, scale_window=1000)

lukesquad = LukeForReadingComprehensionWithLoss(LUKEModel)

lr_schedule = BertLearningRate(learning_rate=15e-6,
                                   end_learning_rate=15e-6 * 0,
                                   warmup_steps=int(data_set.get_dataset_size() * epoch * 0.1),
                                   decay_steps=data_set.get_dataset_size() * epoch,
                                   power=1.0)

update_cell = DynamicLossScaleUpdateCell(loss_scale_value=2 ** 32, scale_factor=2, scale_window=1000)


params = lukesquad.trainable_params()

# lr_schedule
# warmup_steps=877
num_train_steps=14629
warmup_steps = int(epoch * num_train_steps * 0.06)

optimizer = mindspore.nn.AdamWeightDecay(params,
                                         learning_rate=5e-5, #15e-6
                                         beta1=0.9,
                                         beta2=0.98,
                                         eps=1e-06)

# optimizer = mindspore.nn.Adam(params, learning_rate=lr_schedule, eps=1e-8)

optimizer = mindspore.nn.AdamWeightDecay(params,
                                         learning_rate=lr_schedule,
                                         beta1=0.9,
                                         beta2=0.98,
                                         eps=1e-06)


netwithgrads = LukeSquadCell(lukesquad,optimizer=optimizer, scale_update_cell=update_cell)
model = Model(netwithgrads)

loss_monitor = LossCallBack()

In [17]:
model.train(epoch,data_set,callbacks=[loss_monitor],dataset_sink_mode=False)

time: 71626, epoch: 1, step: 1, outputs are (Tensor(shape=[], dtype=Float32, value= 6.25566), Tensor(shape=[], dtype=Bool, value= False))
time: 71968, epoch: 1, step: 2, outputs are (Tensor(shape=[], dtype=Float32, value= 6.24844), Tensor(shape=[], dtype=Bool, value= False))
time: 72310, epoch: 1, step: 3, outputs are (Tensor(shape=[], dtype=Float32, value= 6.2375), Tensor(shape=[], dtype=Bool, value= False))
time: 72646, epoch: 1, step: 4, outputs are (Tensor(shape=[], dtype=Float32, value= 6.23876), Tensor(shape=[], dtype=Bool, value= False))
time: 72976, epoch: 1, step: 5, outputs are (Tensor(shape=[], dtype=Float32, value= 6.23787), Tensor(shape=[], dtype=Bool, value= False))
time: 73301, epoch: 1, step: 6, outputs are (Tensor(shape=[], dtype=Float32, value= 6.18128), Tensor(shape=[], dtype=Bool, value= False))
time: 73624, epoch: 1, step: 7, outputs are (Tensor(shape=[], dtype=Float32, value= 6.22411), Tensor(shape=[], dtype=Bool, value= False))
time: 73948, epoch: 1, step: 8, out

time: 91224, epoch: 1, step: 61, outputs are (Tensor(shape=[], dtype=Float32, value= 6.25203), Tensor(shape=[], dtype=Bool, value= False))
time: 91547, epoch: 1, step: 62, outputs are (Tensor(shape=[], dtype=Float32, value= 6.23543), Tensor(shape=[], dtype=Bool, value= False))
time: 91871, epoch: 1, step: 63, outputs are (Tensor(shape=[], dtype=Float32, value= 6.2362), Tensor(shape=[], dtype=Bool, value= False))
time: 92225, epoch: 1, step: 64, outputs are (Tensor(shape=[], dtype=Float32, value= 6.1638), Tensor(shape=[], dtype=Bool, value= False))
time: 92570, epoch: 1, step: 65, outputs are (Tensor(shape=[], dtype=Float32, value= 6.18667), Tensor(shape=[], dtype=Bool, value= False))
time: 92931, epoch: 1, step: 66, outputs are (Tensor(shape=[], dtype=Float32, value= 6.22741), Tensor(shape=[], dtype=Bool, value= False))
time: 93289, epoch: 1, step: 67, outputs are (Tensor(shape=[], dtype=Float32, value= 6.09099), Tensor(shape=[], dtype=Bool, value= False))
time: 93651, epoch: 1, step: 

time: 110712, epoch: 1, step: 120, outputs are (Tensor(shape=[], dtype=Float32, value= 6.21063), Tensor(shape=[], dtype=Bool, value= False))
time: 111073, epoch: 1, step: 121, outputs are (Tensor(shape=[], dtype=Float32, value= 6.26928), Tensor(shape=[], dtype=Bool, value= False))
time: 111428, epoch: 1, step: 122, outputs are (Tensor(shape=[], dtype=Float32, value= 6.22787), Tensor(shape=[], dtype=Bool, value= False))
time: 111802, epoch: 1, step: 123, outputs are (Tensor(shape=[], dtype=Float32, value= 6.06301), Tensor(shape=[], dtype=Bool, value= False))
time: 112164, epoch: 1, step: 124, outputs are (Tensor(shape=[], dtype=Float32, value= 6.09129), Tensor(shape=[], dtype=Bool, value= False))
time: 112526, epoch: 1, step: 125, outputs are (Tensor(shape=[], dtype=Float32, value= 6.24214), Tensor(shape=[], dtype=Bool, value= False))
time: 112871, epoch: 1, step: 126, outputs are (Tensor(shape=[], dtype=Float32, value= 6.18471), Tensor(shape=[], dtype=Bool, value= False))
time: 113198,

time: 130480, epoch: 1, step: 179, outputs are (Tensor(shape=[], dtype=Float32, value= 6.10909), Tensor(shape=[], dtype=Bool, value= False))
time: 130806, epoch: 1, step: 180, outputs are (Tensor(shape=[], dtype=Float32, value= 6.23073), Tensor(shape=[], dtype=Bool, value= False))
time: 131131, epoch: 1, step: 181, outputs are (Tensor(shape=[], dtype=Float32, value= 6.03041), Tensor(shape=[], dtype=Bool, value= False))
time: 131458, epoch: 1, step: 182, outputs are (Tensor(shape=[], dtype=Float32, value= 6.11049), Tensor(shape=[], dtype=Bool, value= False))
time: 131782, epoch: 1, step: 183, outputs are (Tensor(shape=[], dtype=Float32, value= 5.97732), Tensor(shape=[], dtype=Bool, value= False))
time: 132107, epoch: 1, step: 184, outputs are (Tensor(shape=[], dtype=Float32, value= 6.10547), Tensor(shape=[], dtype=Bool, value= False))
time: 132433, epoch: 1, step: 185, outputs are (Tensor(shape=[], dtype=Float32, value= 6.09302), Tensor(shape=[], dtype=Bool, value= False))
time: 132759,

time: 150104, epoch: 1, step: 238, outputs are (Tensor(shape=[], dtype=Float32, value= 5.82881), Tensor(shape=[], dtype=Bool, value= False))
time: 150429, epoch: 1, step: 239, outputs are (Tensor(shape=[], dtype=Float32, value= 5.74211), Tensor(shape=[], dtype=Bool, value= False))
time: 150754, epoch: 1, step: 240, outputs are (Tensor(shape=[], dtype=Float32, value= 5.86778), Tensor(shape=[], dtype=Bool, value= False))
time: 151079, epoch: 1, step: 241, outputs are (Tensor(shape=[], dtype=Float32, value= 5.67842), Tensor(shape=[], dtype=Bool, value= False))
time: 151408, epoch: 1, step: 242, outputs are (Tensor(shape=[], dtype=Float32, value= 5.89316), Tensor(shape=[], dtype=Bool, value= False))
time: 151750, epoch: 1, step: 243, outputs are (Tensor(shape=[], dtype=Float32, value= 5.37194), Tensor(shape=[], dtype=Bool, value= False))
time: 152078, epoch: 1, step: 244, outputs are (Tensor(shape=[], dtype=Float32, value= 5.72283), Tensor(shape=[], dtype=Bool, value= False))
time: 152403,

...

time: 14154547, epoch: 1, step: 43618, outputs are (Tensor(shape=[], dtype=Float32, value= 1.68651), Tensor(shape=[], dtype=Bool, value= False))
time: 14154870, epoch: 1, step: 43619, outputs are (Tensor(shape=[], dtype=Float32, value= 0.0321156), Tensor(shape=[], dtype=Bool, value= False))
time: 14155192, epoch: 1, step: 43620, outputs are (Tensor(shape=[], dtype=Float32, value= 0.335903), Tensor(shape=[], dtype=Bool, value= False))
time: 14155516, epoch: 1, step: 43621, outputs are (Tensor(shape=[], dtype=Float32, value= 2.11776), Tensor(shape=[], dtype=Bool, value= False))
time: 14155838, epoch: 1, step: 43622, outputs are (Tensor(shape=[], dtype=Float32, value= 1.00341), Tensor(shape=[], dtype=Bool, value= False))
time: 14156159, epoch: 1, step: 43623, outputs are (Tensor(shape=[], dtype=Float32, value= 0.0263035), Tensor(shape=[], dtype=Bool, value= False))
time: 14156482, epoch: 1, step: 43624, outputs are (Tensor(shape=[], dtype=Float32, value= 0.0632419), Tensor(shape=[], dtype

time: 14172920, epoch: 1, step: 43675, outputs are (Tensor(shape=[], dtype=Float32, value= 0.419639), Tensor(shape=[], dtype=Bool, value= False))
time: 14173241, epoch: 1, step: 43676, outputs are (Tensor(shape=[], dtype=Float32, value= 0.918507), Tensor(shape=[], dtype=Bool, value= False))
time: 14173565, epoch: 1, step: 43677, outputs are (Tensor(shape=[], dtype=Float32, value= 0.308658), Tensor(shape=[], dtype=Bool, value= False))
time: 14173887, epoch: 1, step: 43678, outputs are (Tensor(shape=[], dtype=Float32, value= 0.976417), Tensor(shape=[], dtype=Bool, value= False))
time: 14174208, epoch: 1, step: 43679, outputs are (Tensor(shape=[], dtype=Float32, value= 0.21751), Tensor(shape=[], dtype=Bool, value= False))
time: 14174532, epoch: 1, step: 43680, outputs are (Tensor(shape=[], dtype=Float32, value= 1.77297), Tensor(shape=[], dtype=Bool, value= False))
time: 14174855, epoch: 1, step: 43681, outputs are (Tensor(shape=[], dtype=Float32, value= 0.35916), Tensor(shape=[], dtype=Bo

time: 14191306, epoch: 1, step: 43732, outputs are (Tensor(shape=[], dtype=Float32, value= 0.169992), Tensor(shape=[], dtype=Bool, value= False))
time: 14191628, epoch: 1, step: 43733, outputs are (Tensor(shape=[], dtype=Float32, value= 0.0185472), Tensor(shape=[], dtype=Bool, value= False))
time: 14191950, epoch: 1, step: 43734, outputs are (Tensor(shape=[], dtype=Float32, value= 0.732882), Tensor(shape=[], dtype=Bool, value= False))
time: 14192273, epoch: 1, step: 43735, outputs are (Tensor(shape=[], dtype=Float32, value= 0.161417), Tensor(shape=[], dtype=Bool, value= False))
time: 14192594, epoch: 1, step: 43736, outputs are (Tensor(shape=[], dtype=Float32, value= 1.55018), Tensor(shape=[], dtype=Bool, value= False))
time: 14192916, epoch: 1, step: 43737, outputs are (Tensor(shape=[], dtype=Float32, value= 0.27502), Tensor(shape=[], dtype=Bool, value= False))
time: 14193238, epoch: 1, step: 43738, outputs are (Tensor(shape=[], dtype=Float32, value= 0.145054), Tensor(shape=[], dtype=

time: 14209671, epoch: 1, step: 43789, outputs are (Tensor(shape=[], dtype=Float32, value= 0.154989), Tensor(shape=[], dtype=Bool, value= False))
time: 14209993, epoch: 1, step: 43790, outputs are (Tensor(shape=[], dtype=Float32, value= 0.0214957), Tensor(shape=[], dtype=Bool, value= False))
time: 14210316, epoch: 1, step: 43791, outputs are (Tensor(shape=[], dtype=Float32, value= 0.347194), Tensor(shape=[], dtype=Bool, value= False))
time: 14210637, epoch: 1, step: 43792, outputs are (Tensor(shape=[], dtype=Float32, value= 0.841347), Tensor(shape=[], dtype=Bool, value= False))
time: 14210959, epoch: 1, step: 43793, outputs are (Tensor(shape=[], dtype=Float32, value= 2.04859), Tensor(shape=[], dtype=Bool, value= False))
time: 14211283, epoch: 1, step: 43794, outputs are (Tensor(shape=[], dtype=Float32, value= 0.150379), Tensor(shape=[], dtype=Bool, value= False))
time: 14211605, epoch: 1, step: 43795, outputs are (Tensor(shape=[], dtype=Float32, value= 0.154421), Tensor(shape=[], dtype

time: 14228031, epoch: 1, step: 43846, outputs are (Tensor(shape=[], dtype=Float32, value= 1.16179), Tensor(shape=[], dtype=Bool, value= False))
time: 14228355, epoch: 1, step: 43847, outputs are (Tensor(shape=[], dtype=Float32, value= 0.368419), Tensor(shape=[], dtype=Bool, value= False))
time: 14228677, epoch: 1, step: 43848, outputs are (Tensor(shape=[], dtype=Float32, value= 0.0490321), Tensor(shape=[], dtype=Bool, value= False))
time: 14228998, epoch: 1, step: 43849, outputs are (Tensor(shape=[], dtype=Float32, value= 0.211185), Tensor(shape=[], dtype=Bool, value= False))
time: 14229322, epoch: 1, step: 43850, outputs are (Tensor(shape=[], dtype=Float32, value= 1.2052), Tensor(shape=[], dtype=Bool, value= False))
time: 14229644, epoch: 1, step: 43851, outputs are (Tensor(shape=[], dtype=Float32, value= 0.492707), Tensor(shape=[], dtype=Bool, value= False))
time: 14229965, epoch: 1, step: 43852, outputs are (Tensor(shape=[], dtype=Float32, value= 0.163111), Tensor(shape=[], dtype=B

In [18]:

save_checkpoint(model.train_network.network.net, "ft.ckpt")